In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import shap
import os
import pickle

import warnings
warnings.filterwarnings('ignore')

from sklearn.linear_model import LinearRegression
from sklearn.svm import SVR
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import ElasticNet
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import AdaBoostRegressor
from sklearn.ensemble import GradientBoostingRegressor
from lightgbm import LGBMRegressor

from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error, r2_score

c:\Users\ishan\AppData\Local\Programs\Python\Python310\lib\site-packages\shap\utils\_clustering.py:35: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  def _pt_shuffle_rec(i, indexes, index_mask, partition_tree, M, pos):
c:\Users\ishan\AppData\Local\Programs\Python\Python310\lib\site-packages\shap\utils\_clustering.py:54: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.

In [2]:
df = pd.read_csv('MVP_Candidates.csv')
df.fillna(0)

Unnamed: 0.1  Unnamed: 0                 Player Pos  Pos_No  Age   Tm  \
0               0           0           Nikola Jokić   C       5   26  DEN   
1               1           1            Joel Embiid   C       5   27  PHI   
2               2           2  Giannis Antetokounmpo  PF       4   27  MIL   
3               3           3           Devin Booker  SG       2   25  PHO   
4               4           4            Luka Dončić  PG       1   22  DAL   
..            ...         ...                    ...  ..     ...  ...  ...   
481           481         481           Bernard King  SF       3   34  WSB   
482           482         482            Kenny Smith  PG       1   25  HOU   
483           483         483        Hakeem Olajuwon   C       5   28  HOU   
484           484         484           Tim Hardaway  PG       1   24  GSW   
485           485         485           Kevin McHale  PF       4   33  BOS   

      G  GS  Seed  ...  6.FT+  6.TS+  6.FTr+  6.3PAr+  6.FG Add  6.TS Add  \
0    74  74    10  ...    105    117     144     55.0     230.9     286.9   
1    68  68     8  ...    105    109     243     47.0       6.5     169.0   
2    67  67     7  ...     93    112     248     49.0     125.1     211.1   
3    68  68     1  ...    112    102     103     84.0      -4.1      32.6   
4    65  65     5  ...     96    101     140    102.0      -8.9      15.3   
..   ..  ..   ...  ...    ...    ...     ...      ...       ...       ...   
481  64  64    20  ...    103     99     100     30.0     -38.6     -26.0   
482  78  78     8  ...    110    112     106    164.0     115.5     148.1   
483  56  50     8  ...    101    103      90      5.0      39.4      31.8   
484  82  82    11  ...    105    102      77    198.0      63.4      44.2   
485  68  10     4  ...    108    113      94     50.0     134.2     146.9   

     MVP  MVP Rank  MVP Share     Year  
0      1         1      0.875  2021-22  
1      0         2      0.706  2021-22  
2      0         3      0.595  2021-22  
3      0         4      0.216  2021-22  
4      0         5      0.146  2021-22  
..   ...       ...        ...      ...  
481    0        16      0.007  1990-91  
482    0        17      0.005  1990-91  
483    0        18      0.004  1990-91  
484    0        19      0.001  1990-91  
485    0        19      0.001  1990-91  

[486 rows x 122 columns]

In [3]:
'''
1990-91 to 1998-99
1999-00 to 2011-12
2012-13 to 2021-22
'''
e1 = ('2021-22', '2020-21', '2019-20', '2018-19', '2017-18', '2016-17', '2015-16', '2014-15', '2013-14', '2012-13')
e2 = ('2011-12', '2010-09', '2008-09', '2007-08', '2006-07', '2005-06', '2004-05', '2003-04', '2002-03', '2001-02', '2000-01', '1999-00')
e3 = ('1998-99', '1997-98', '1996-97', '1995-96', '1994-95', '1993-94', '1992-93', '1991-92', '1990-91')


df1 = df[(df['Year'] == '2021-22') | (df['Year'] == '2020-21') | (df['Year'] == '2019-20') | (df['Year'] == '2018-19') | (df['Year'] == '2017-18') | (df['Year'] == '2016-17') | (df['Year'] == '2015-16') | (df['Year'] == '2014-15') | (df['Year'] == '2013-14') | (df['Year'] == '2012-13')]


In [4]:
df1

Unnamed: 0.1  Unnamed: 0                 Player Pos  Pos_No  Age   Tm  \
0               0           0           Nikola Jokić   C       5   26  DEN   
1               1           1            Joel Embiid   C       5   27  PHI   
2               2           2  Giannis Antetokounmpo  PF       4   27  MIL   
3               3           3           Devin Booker  SG       2   25  PHO   
4               4           4            Luka Dončić  PG       1   22  DAL   
..            ...         ...                    ...  ..     ...  ...  ...   
125           125         125          Kevin Garnett   C       5   36  BOS   
126           126         126             Marc Gasol   C       5   28  MEM   
127           127         127              Ty Lawson  PG       1   25  DEN   
128           128         128              David Lee  PF       4   29  GSW   
129           129         129            Joakim Noah   C       5   27  CHI   

      G  GS  Seed  ...  6.FT+  6.TS+  6.FTr+  6.3PAr+  6.FG Add  6.TS Add  \
0    74  74    10  ...    105    117     144     55.0     230.9     286.9   
1    68  68     8  ...    105    109     243     47.0       6.5     169.0   
2    67  67     7  ...     93    112     248     49.0     125.1     211.1   
3    68  68     1  ...    112    102     103     84.0      -4.1      32.6   
4    65  65     5  ...     96    101     140    102.0      -8.9      15.3   
..   ..  ..   ...  ...    ...    ...     ...      ...       ...       ...   
125  68  68    16  ...    104    100      87      8.0       2.1       0.6   
126  80  80     6  ...    113    105     134      7.0      -3.8      49.2   
127  73  71     4  ...    100    103     118     98.0      16.9      31.5   
128  79  79    10  ...    106    105     102      1.0      52.3      68.1   
129  66  64    11  ...    100    100     139      3.0     -19.5      -1.1   

     MVP  MVP Rank  MVP Share     Year  
0      1         1      0.875  2021-22  
1      0         2      0.706  2021-22  
2      0         3      0.595  2021-22  
3      0         4      0.216  2021-22  
4      0         5      0.146  2021-22  
..   ...       ...        ...      ...  
125    0        12      0.001  2012-13  
126    0        12      0.001  2012-13  
127    0        12      0.001  2012-13  
128    0        12      0.001  2012-13  
129    0        12      0.001  2012-13  

[130 rows x 122 columns]

In [5]:
df1.drop(df1.columns[[0, 1]], axis = 1, inplace=True)

In [6]:
df1['6.3P+'][108] = 0
''' WHY WAS THIS NaN I HAVE NO CLUE - FILLNA SHOULD HAVE MADE IT ZERO '''
''' ANYWAY PROBLEM SOLVED '''

' ANYWAY PROBLEM SOLVED '

In [7]:
df1.to_csv('ModernEra.csv', index=False)

In [8]:
df1

Player Pos  Pos_No  Age   Tm   G  GS  Seed     Win %  \
0             Nikola Jokić   C       5   26  DEN  74  74    10  0.585366   
1              Joel Embiid   C       5   27  PHI  68  68     8  0.621951   
2    Giannis Antetokounmpo  PF       4   27  MIL  67  67     7  0.621951   
3             Devin Booker  SG       2   25  PHO  68  68     1  0.780488   
4              Luka Dončić  PG       1   22  DAL  65  65     5  0.634146   
..                     ...  ..     ...  ...  ...  ..  ..   ...       ...   
125          Kevin Garnett   C       5   36  BOS  68  68    16  0.506173   
126             Marc Gasol   C       5   28  MEM  80  80     6  0.682927   
127              Ty Lawson  PG       1   25  DEN  73  71     4  0.695122   
128              David Lee  PF       4   29  GSW  79  79    10  0.573171   
129            Joakim Noah   C       5   27  CHI  66  64    11  0.548780   

     1.MP  ...  6.FT+  6.TS+  6.FTr+  6.3PAr+  6.FG Add  6.TS Add  MVP  \
0    2476  ...    105    117     144     55.0     230.9     286.9    1   
1    2297  ...    105    109     243     47.0       6.5     169.0    0   
2    2204  ...     93    112     248     49.0     125.1     211.1    0   
3    2345  ...    112    102     103     84.0      -4.1      32.6    0   
4    2301  ...     96    101     140    102.0      -8.9      15.3    0   
..    ...  ...    ...    ...     ...      ...       ...       ...  ...   
125  2022  ...    104    100      87      8.0       2.1       0.6    0   
126  2796  ...    113    105     134      7.0      -3.8      49.2    0   
127  2513  ...    100    103     118     98.0      16.9      31.5    0   
128  2907  ...    106    105     102      1.0      52.3      68.1    0   
129  2426  ...    100    100     139      3.0     -19.5      -1.1    0   

     MVP Rank  MVP Share     Year  
0           1      0.875  2021-22  
1           2      0.706  2021-22  
2           3      0.595  2021-22  
3           4      0.216  2021-22  
4           5      0.146  2021-22  
..        ...        ...      ...  
125        12      0.001  2012-13  
126        12      0.001  2012-13  
127        12      0.001  2012-13  
128        12      0.001  2012-13  
129        12      0.001  2012-13  

[130 rows x 120 columns]

In [9]:
def calc_metrics(y_test, y_pred):
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    r2 = r2_score(y_test, y_pred)
    return rmse, r2

In [10]:
# Testing Seasons - 2014-15, 2019-20
# Testing Rows -> 85-96, 27-38

testing_data = df1.iloc[27:39].append(df1.iloc[85:97])

In [11]:
training_data = df1.iloc[0:27].append(df1.iloc[39:85]).append(df1.iloc[97:])

In [12]:
col_to_drop = []
for i in df1.columns:
    if i[0] == '3' or i[0] == '4':
        col_to_drop.append(i)

In [13]:
X_train = training_data.drop(['Player', 'Pos', 'Tm', 'MVP', 'MVP Rank', 'MVP Share', 'Year'] + col_to_drop, axis=1)
Y_train = training_data['MVP Share']

In [14]:
X_test = testing_data.drop(['Player', 'Pos', 'Tm', 'MVP', 'MVP Rank', 'MVP Share', 'Year'] + col_to_drop
                           , axis=1)
Y_test = testing_data['MVP Share']

In [15]:
scaler = StandardScaler()
scaled_X_train = scaler.fit_transform(X_train)
scaled_X_test = scaler.transform(X_test)

In [16]:
final_params = []

In [17]:
param_grid = {'learning_rate':[0.01,0.1,0.2,0.3],
                'num_leaves':[5,10,20,30],
                'min_data_in_leaf':[10,25,50],
                'max_depth':[2,3,4],
                'feature_fraction':[0.6,0.7,0.8,0.9],
                'min_gain_to_split':[0,0.01,0.1,0.2],
                'verbose':[-1]}
lgbm_model = LGBMRegressor()
grid = GridSearchCV(lgbm_model, param_grid)
grid.fit(scaled_X_train, Y_train)
model = LGBMRegressor(**grid.best_params_)
final_params.append(grid.best_params_)

[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=10, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=10
[LightGBM] [Warning] min_gain_to_split is set=0, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=10, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=10
[LightGBM] [Warning] min_gain_to_split is set=0, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=10, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=10
[LightGBM] [Warning] m

In [18]:
model.fit(scaled_X_train, Y_train)

LGBMRegressor(feature_fraction=0.6, max_depth=2, min_data_in_leaf=10,
              min_gain_to_split=0, num_leaves=5, verbose=-1)

In [19]:
Y_pred = model.predict(scaled_X_test)

In [20]:
print(Y_pred)

[0.72787698 0.12378224 0.58996182 0.12145102 0.11914656 0.10470887
 0.03705996 0.00327378 0.08468681 0.03370586 0.08884387 0.0314186
 0.61955    0.56333042 0.0242257  0.41786536 0.55201383 0.35519157
 0.06480675 0.03865839 0.07689999 0.03206151 0.04224246 0.04851221]


In [21]:
initial_results = testing_data[['Player','Year','MVP Share','MVP Rank']]
results = initial_results.copy()
results['Predicted MVP Share'] = pd.Series(Y_pred).values
results = results.sort_values(['Year', 'Predicted MVP Share'], ascending=[False, False]).reset_index(drop=True)
test_season1 = results[(results['Year'] == '2019-20')].reset_index(drop=True)
test_season2 = results[(results['Year'] == '2014-15')].reset_index(drop=True)
test_season1['MVP Rank'] = test_season1.index + 1
test_season2['MVP Rank'] = test_season2.index + 1

In [22]:
print(test_season1)

                   Player     Year  MVP Share  MVP Rank  Predicted MVP Share
0   Giannis Antetokounmpo  2019-20      0.952         1             0.727877
1            James Harden  2019-20      0.363         2             0.589962
2            LeBron James  2019-20      0.746         3             0.123782
3             Luka Dončić  2019-20      0.198         4             0.121451
4           Kawhi Leonard  2019-20      0.166         5             0.119147
5           Anthony Davis  2019-20      0.081         6             0.104709
6            Jimmy Butler  2019-20      0.009         7             0.088844
7            Nikola Jokić  2019-20      0.018         8             0.084687
8              Chris Paul  2019-20      0.026         9             0.037060
9           Pascal Siakam  2019-20      0.017        10             0.033706
10           Jayson Tatum  2019-20      0.001        11             0.031419
11         Damian Lillard  2019-20      0.023        12             0.003274

In [23]:
print(test_season2)

               Player     Year  MVP Share  MVP Rank  Predicted MVP Share
0       Stephen Curry  2014-15      0.922         1             0.619550
1        James Harden  2014-15      0.720         2             0.563330
2       Anthony Davis  2014-15      0.156         3             0.552014
3   Russell Westbrook  2014-15      0.271         4             0.417865
4          Chris Paul  2014-15      0.095         5             0.355192
5       Blake Griffin  2014-15      0.002         6             0.076900
6   LaMarcus Aldridge  2014-15      0.005         7             0.064807
7       Klay Thompson  2014-15      0.001         8             0.048512
8       Kawhi Leonard  2014-15      0.001         9             0.042242
9          Marc Gasol  2014-15      0.002        10             0.038658
10         Tim Duncan  2014-15      0.001        11             0.032062
11       LeBron James  2014-15      0.425        12             0.024226


In [24]:
rmse, r2 = calc_metrics(Y_test, Y_pred)
print("RMSE = ", rmse)
print("R2 = ", r2)

RMSE =  0.20899004572686528
R2 =  0.5232343376091633
